# SENTIMENT ANALYSIS FOR COMMENTS OF USERS USING LLM's

## START BY LOADING IMDB DATASET REVIEWS

###  IMPLEMENT A BASELINE MODEL LOGISTIC REGRESSION FOR CLASSIFICATION OF COMMENTS

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
# Load the data path of the dataset
data_path = 'datasets/IMDB_Dataset_Sentiment.csv'
df1 = pd.read_csv(data_path)
print(f'The initial length of the IMDB dataset is: {len(df1)}')
print(f'The columns of the IMDB dataset are: {df1.columns}')

text_column = 'review'
label_column = 'sentiment'

all_comments = [comment for comment in df1[text_column]]
all_labels= [label for label in df1[label_column]]
# Split the dataset and take the half
X, _, y, _ = train_test_split(all_comments, all_labels, test_size=0.5, random_state=42, stratify=all_labels)
print(f'the length of the dataset is {len(X)}')

The initial length of the IMDB dataset is: 50000
The columns of the IMDB dataset are: Index(['review', 'sentiment'], dtype='object')
the length of the dataset is 25000


In [2]:
import re

def remove_html_tags(text):
    """
    Remove HTML tags from a string.

    Parameters:
    - text (str): The string containing HTML tags.

    Returns:
    - clean_text (str): The string with HTML tags removed.
    """
    # Regular expression pattern to identify HTML tags
    clean_text = re.sub(r'<[^>]+>', '', text)
    return clean_text

X = [str(remove_html_tags(comment)) for comment in X]
print(f'A sample of the cleaned dataset is:\n{X[10]}')

# Split the dataset into training and test set
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)
print(f'The length of the training dataset is: {len(x_train)}')

A sample of the cleaned dataset is:
The greatest Tarzan ever made! This movie is done in a way that no other Tarzan ever has come close in doing. It has every thing in it that you would want in a Tarzan movie. No other Tarzan movie ever has or ever will portray the character this well. I would say that if you have seen a Tarzan movie and liked it you should see this one you will love it, and if you have never seen Tarzan you should see this one and forget the rest of them.
The length of the training dataset is: 20000


### TRAIN AND EVALUATE THE LOGISTIC REGRESSION MODEL

In [11]:
from models.LR_Classifier import prepare_data_LR, train_logistic_regression, evaluate_logistic_regression
# Step 1: Prepare the data for LR model
x_train_LR, x_test_LR = prepare_data_LR(x_train, x_test)

# Step 2: Train the model
model = train_logistic_regression(x_train_LR, y_train)

# Step 3: Evaluate the model
LR_report = evaluate_logistic_regression(model, x_test_LR, y_test)

              precision    recall  f1-score   support

    negative       0.87      0.87      0.87      2500
    positive       0.87      0.87      0.87      2500

    accuracy                           0.87      5000
   macro avg       0.87      0.87      0.87      5000
weighted avg       0.87      0.87      0.87      5000



### IMPLEMENT A MORE ACCURATE MODEL FOR CLASSIFICATION OF COMMENTS - BERT IMPLEMENTATION

In [12]:
import torch
import pytorch_lightning as pl
from pytorch_lightning.callbacks import LearningRateMonitor
from pytorch_lightning.callbacks import ModelCheckpoint
from pytorch_lightning.callbacks import RichProgressBar
from pytorch_lightning.callbacks.early_stopping import EarlyStopping

from transformers import BertTokenizer, BertForSequenceClassification
from models.transformer_classifier import tokenize_data, create_dataloaders, TransformerClassifier

# Load pre-trained transformer model and the tokenizer
model_name = 'bert-base-uncased'
tokenizer = BertTokenizer.from_pretrained(model_name)
model = BertForSequenceClassification.from_pretrained(model_name, num_labels=2)

# transform label in digits
y_train = [0 if label == 'positive' else 1 for label in y_train]
y_test = [0 if label == 'positive' else 1 for label in y_test]

# Prepare data for Transformer model
train_tokenizer, train_labels = tokenize_data(tokenizer, x_train, y_train)
test_tokenizer, test_labels = tokenize_data(tokenizer, x_test, y_test)

# Create DataLoader for training and validation data
batch_size = 32
train_dataloader = create_dataloaders(train_tokenizer, train_labels, batch_size=batch_size, is_training_set=True)
test_dataloader = create_dataloaders(test_tokenizer, test_labels, batch_size=batch_size,  is_training_set=False)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [13]:
# Initialize PyTorch Lightning model
bert_model = TransformerClassifier(model)

# Define callbacks
checkpoint_cb = ModelCheckpoint(
    dirpath="bert_checkpoints",
    filename="imdb_{epoch}-val_acc={val_acc:.4f}",
    monitor="val_loss",
    verbose=True,
    save_last=True,
    save_top_k=1,
    mode="min",
    auto_insert_metric_name=False,
    save_weights_only=False,
    every_n_epochs=1,
)
es_cb = EarlyStopping(patience=3, monitor="val_loss", mode="min")
lr_cb = LearningRateMonitor(logging_interval="epoch", log_momentum=False)

# Define the trainer using PyTorch Lightning Trainer
device = 'gpu' if torch.cuda.is_available() else 'auto'
trainer = pl.Trainer(max_epochs=3, 
                    devices=1,
                    accelerator=device,
                    callbacks=[checkpoint_cb, es_cb, lr_cb, RichProgressBar()])

# Train the model
trainer.fit(bert_model, train_dataloader, test_dataloader)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
C:\1. Python\LLM_mods_Research\venv\Lib\site-packages\pytorch_lightning\callbacks\model_checkpoint.py:654: Checkpoint directory C:\1. Python\LLM_mods_Research\bert_checkpoints exists and is not empty.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


┏━━━┳━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━┳━━━━━━┓
┃   ┃ Name  ┃ Type                          ┃ Params ┃ Mode ┃
┡━━━╇━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━╇━━━━━━┩
│ 0 │ model │ BertForSequenceClassification │  109 M │ eval │
└───┴───────┴───────────────────────────────┴────────┴──────┘

Trainable params: 85.6 M                                                                                           
Non-trainable params: 23.8 M                                                                                       
Total params: 109 M                                                                                                
Total estimated model params size (MB): 437                                                                        
Modules in train mode: 0                                                                                           
Modules in eval mode: 231

Output()

Epoch 0, global step 625: 'val_loss' reached 0.21682 (best 0.21682), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\0-val_acc=0.9124.ckpt' as top 1
Epoch 1, global step 1250: 'val_loss' was not in top 1
Epoch 2, global step 1875: 'val_loss' was not in top 1
`Trainer.fit` stopped: `max_epochs=3` reached.


In [14]:
from sklearn.metrics import classification_report

# Assuming `trainer` is your Trainer object and `model` is your trained LightningModule
predictions = trainer.predict(bert_model, test_dataloader)

all_preds = []
all_labels = []

# Assuming each prediction output contains a dict with 'preds' and 'labels' keys as in your model's validation_step
for output in predictions:
    preds = output['preds'].cpu()
    labels = output['labels'].cpu()
    all_preds.append(preds)
    all_labels.append(labels)

# Concatenate all the tensors
all_preds = torch.cat(all_preds)
all_labels = torch.cat(all_labels)

# Convert tensors to numpy arrays if needed
all_preds = all_preds.numpy()
all_labels = all_labels.numpy()

# Generate the report
bert_report = classification_report(all_labels, all_preds, target_names=['positive', 'negative'])
print(bert_report)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Output()

              precision    recall  f1-score   support

    positive       0.87      0.95      0.91      2500
    negative       0.94      0.86      0.90      2500

    accuracy                           0.91      5000
   macro avg       0.91      0.91      0.91      5000
weighted avg       0.91      0.91      0.91      5000



### CLASSIFICATION OF COMMENTS WITH GPT MODELS

#### FIRST ATTEMPT WITH GPT-4o

In [3]:
from models.LLM_Classifier import GPT_Classifier, validate_GPT_model

pred_labels_GPT = GPT_Classifier(x_test, name_of_prompt='prompt_for_classification_imdb', GPT_model='gpt-4o')

  0%|                                                                                                                                           | 1/5000 [00:01<2:09:06,  1.55s/it]

0
Chosen label from GPT model is: 0


  0%|                                                                                                                                           | 2/5000 [00:02<1:38:06,  1.18s/it]

0
Chosen label from GPT model is: 0


  0%|                                                                                                                                           | 3/5000 [00:03<1:28:51,  1.07s/it]

...

  0%|▏                                                                                                                                          | 5/5000 [00:04<1:13:57,  1.13it/s]

0
Chosen label from GPT model is: 0


  0%|▏                                                                                                                                          | 6/5000 [00:05<1:03:17,  1.32it/s]

1
Chosen label from GPT model is: 1


  0%|▏                                                                                                                                          | 6/5000 [00:05<1:21:31,  1.02it/s]

KeyboardInterrupt



In [14]:
pred_labels_GPT_transformed = []
for idx in range(len(pred_labels_GPT)):
    if pred_labels_GPT[idx] == 0:
        pred_labels_GPT_transformed.append('positive')
    else:
        pred_labels_GPT_transformed.append('negative')
    
cls_report_GPT = validate_GPT_model(y_test, pred_labels_GPT_transformed)

              precision    recall  f1-score   support

    negative       0.94      0.98      0.96      2500
    positive       0.97      0.93      0.95      2500

    accuracy                           0.95      5000
   macro avg       0.96      0.95      0.95      5000
weighted avg       0.96      0.95      0.95      5000



#### SECOND ATTEMPT WITH GPT-4o-mini

In [8]:
from models.LLM_Classifier import GPT_Classifier, validate_GPT_model

pred_labels_GPT_mini = GPT_Classifier(x_test, name_of_prompt='prompt_for_classification_imdb', GPT_model='gpt-4o-mini')

  0%|                                                                                                                                           | 1/5000 [00:01<1:26:34,  1.04s/it]

0
Chosen label from GPT model is: 0


  0%|                                                                                                                                           | 2/5000 [00:01<1:02:42,  1.33it/s]

0
Chosen label from GPT model is: 0


  0%|                                                                                                                                           | 3/5000 [00:02<1:00:56,  1.37it/s]

...

1
Chosen label from GPT model is: 1


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 4999/5000 [44:18<00:00,  2.11it/s]

0
Chosen label from GPT model is: 0


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5000/5000 [44:19<00:00,  1.88it/s]

0
Chosen label from GPT model is: 0


In [9]:
pred_labels_GPT_transformed_mini = []
for idx in range(len(pred_labels_GPT_mini)):
    if pred_labels_GPT_mini[idx] == 0:
        pred_labels_GPT_transformed_mini.append('positive')
    else:
        pred_labels_GPT_transformed_mini.append('negative')
    
cls_report_GPT = validate_GPT_model(y_test, pred_labels_GPT_transformed_mini)

              precision    recall  f1-score   support

    negative       0.91      0.98      0.94      2500
    positive       0.97      0.90      0.94      2500

    accuracy                           0.94      5000
   macro avg       0.94      0.94      0.94      5000
weighted avg       0.94      0.94      0.94      5000



#### THIRD ATTEMPT WITH GPT-3.5-turbo

In [ ]:
from models.LLM_Classifier import GPT_Classifier, validate_GPT_model

pred_labels_GPT_3_5 = GPT_Classifier(x_test[:1000], name_of_prompt='prompt_for_classification_imdb', GPT_model='gpt-3.5-turbo')

In [3]:
pred_labels_GPT_transformed_3_5 = []
for idx in range(len(pred_labels_GPT_3_5)):
    if pred_labels_GPT_3_5[idx] == 0:
        pred_labels_GPT_transformed_3_5.append('positive')
    else:
        pred_labels_GPT_transformed_3_5.append('negative')
        
    
cls_report_GPT = validate_GPT_model(y_test[:500], pred_labels_GPT_transformed_3_5)

NameError: name 'pred_labels_GPT_3_5' is not defined

## LOAD THE SECOND DATASET WHICH IS AIRLINE DATASET REVIEWS 

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
# Load the data path of the dataset
data_path2 = 'datasets/airline_sentiment_reviews/Tweets.csv'
df2 = pd.read_csv(data_path2)
print(f'The initial length of the Airline reviews dataset is: {len(df2)}')
print(f'The columns of the Airline reviews dataset are: {df2.columns}')
print(df2[['airline_sentiment','text']].sample())

The initial length of the Airline reviews dataset is: 14640
The columns of the Airline reviews dataset are: Index(['tweet_id', 'airline_sentiment', 'airline_sentiment_confidence',
       'negativereason', 'negativereason_confidence', 'airline',
       'airline_sentiment_gold', 'name', 'negativereason_gold',
       'retweet_count', 'text', 'tweet_coord', 'tweet_created',
       'tweet_location', 'user_timezone'],
      dtype='object')
    airline_sentiment                                               text
159          negative  @VirginAmerica I rang, but there is a wait for...


In [2]:
print(df2.loc[5180:5200, ['text', 'airline_sentiment']])

                                                   text airline_sentiment
5180  @SouthwestAir lost bag on flight to Vegas. Now...          negative
5181  @SouthwestAir breaking my heart at BWI 9 hrs @...          negative
5182  @SouthwestAir Officially a customer support ga...          negative
5183  @SouthwestAir  also, gave up after 1 hr 32 min...          negative
5184  @SouthwestAir 3 + hrs w/out bags being returne...          negative
5185  @SouthwestAir I had to switch airlines and eat...          negative
5186  @SouthwestAir Great #BlackHistoryMonth commerc...          positive
5187  @SouthwestAir well I'm not sure what there is ...          negative
5188  @SouthwestAir is now recruiting for Fall 15, S...           neutral
5189  @SouthwestAir There is no way that I am gettin...          negative
5190  @SouthwestAir AH - did DM, no reply. On hold n...          negative
5191  @SouthwestAir replacing @vitaminwater with bee...          positive
5192  @SouthwestAir  reservation (FEHQ

In [3]:
print(df2.loc[5191, 'text']) # the positive comment
print(df2.loc[5194, 'text']) # the positive comment
print(df2.loc[5200, 'text']) # the neutral comment
print(df2.loc[5197, 'text']) # another neutral comment
print(df2.loc[5190, 'text']) # the negative comment

@SouthwestAir replacing @vitaminwater with beer! Bravo!👏👏 Cheers! 🍻🍻 @Leinenkugels @DosEquis @FatTire
@SouthwestAir i hope i can be apart of the team with this job opening!
@SouthwestAir i like to see if i can change flight plz help thx
@SouthwestAir How can you get your TSA traveler ID added to your boarding pass? Why would it not be included as TSA precheck? Flying tomorro
@SouthwestAir AH - did DM, no reply. On hold now over 2hrs. Just spent over $1k to get a United flight tmrw to get home. #lame


In [4]:
text_column = 'text'
label_column = 'airline_sentiment'

all_comments = [comment for comment in df2[text_column]]
all_labels= [label for label in df2[label_column]]
# Split the dataset and take the 80%
X, _, y, _ = train_test_split(all_comments, all_labels, test_size=0.2, random_state=42, stratify=all_labels)
print(f'the length of the dataset is {len(X)}')

# Split the dataset into training and test set
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)
print(f'The length of the training dataset is: {len(x_train)}')

the length of the dataset is 11712
The length of the training dataset is: 9369


### IMPLEMENT A BASELINE MODEL LOGISTIC REGRESSION FOR CLASSIFICATION OF COMMENTS

In [5]:
from models.LR_Classifier import prepare_data_LR, train_logistic_regression, evaluate_logistic_regression
# Step 1: Prepare the data for LR model
x_train_LR, x_test_LR = prepare_data_LR(x_train, x_test)

# Step 2: Train the model
model = train_logistic_regression(x_train_LR, y_train)

# Step 3: Evaluate the model
LR_report = evaluate_logistic_regression(model, x_test_LR, y_test)

              precision    recall  f1-score   support

    negative       0.86      0.88      0.87      1469
     neutral       0.63      0.61      0.62       496
    positive       0.74      0.67      0.70       378

    accuracy                           0.79      2343
   macro avg       0.74      0.72      0.73      2343
weighted avg       0.79      0.79      0.79      2343



### IMPLEMENT A MORE ACCURATE MODEL FOR CLASSIFICATION OF COMMENTS - BERT IMPLEMENTATION

In [6]:
import torch
import pytorch_lightning as pl
from pytorch_lightning.callbacks import LearningRateMonitor
from pytorch_lightning.callbacks import ModelCheckpoint
from pytorch_lightning.callbacks import RichProgressBar
from pytorch_lightning.callbacks.early_stopping import EarlyStopping

from transformers import BertTokenizer, BertForSequenceClassification
from models.transformer_classifier import tokenize_data, create_dataloaders, TransformerClassifier

# Load pre-trained transformer model and the tokenizer
model_name = 'bert-base-uncased'
tokenizer = BertTokenizer.from_pretrained(model_name)
model = BertForSequenceClassification.from_pretrained(model_name, num_labels=3)

# Assuming your labels are 'positive', 'negative', and 'neutral'
y_train = [0 if label == 'positive' else 2 if label == 'negative' else 1 for label in y_train]
y_test = [0 if label == 'positive' else 2 if label == 'negative' else 1 for label in y_test]


# Prepare data for Transformer model
train_tokenizer, train_labels = tokenize_data(tokenizer, x_train, y_train)
test_tokenizer, test_labels = tokenize_data(tokenizer, x_test, y_test)

# Create DataLoader for training and validation data
batch_size = 32
train_dataloader = create_dataloaders(train_tokenizer, train_labels, batch_size=batch_size, is_training_set=True)
test_dataloader = create_dataloaders(test_tokenizer, test_labels, batch_size=batch_size,  is_training_set=False)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [7]:
# Initialize PyTorch Lightning model
bert_model = TransformerClassifier(model, learning_rate=1e-6)

# Define callbacks
checkpoint_cb = ModelCheckpoint(
    dirpath="bert_checkpoints",
    filename="{epoch}-val_acc={val_acc:.4f}",
    monitor="val_loss",
    verbose=True,
    save_last=True,
    save_top_k=1,
    mode="min",
    auto_insert_metric_name=False,
    save_weights_only=False,
    every_n_epochs=1,
)
es_cb = EarlyStopping(patience=4, monitor="val_loss", mode="min")
lr_cb = LearningRateMonitor(logging_interval="epoch", log_momentum=False)

# Define the trainer using PyTorch Lightning Trainer
device = 'gpu' if torch.cuda.is_available() else 'auto'
trainer = pl.Trainer(max_epochs=20, 
                    devices=1,
                    accelerator=device,
                    callbacks=[checkpoint_cb, es_cb, lr_cb, RichProgressBar()])

# Train the model
trainer.fit(bert_model, train_dataloader, test_dataloader)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
C:\1. Python\LLM_mods_Research\venv\Lib\site-packages\pytorch_lightning\callbacks\model_checkpoint.py:654: Checkpoint directory C:\1. Python\LLM_mods_Research\bert_checkpoints exists and is not empty.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


┏━━━┳━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━┳━━━━━━┓
┃   ┃ Name  ┃ Type                          ┃ Params ┃ Mode ┃
┡━━━╇━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━╇━━━━━━┩
│ 0 │ model │ BertForSequenceClassification │  109 M │ eval │
└───┴───────┴───────────────────────────────┴────────┴──────┘

Trainable params: 85.6 M                                                                                           
Non-trainable params: 23.8 M                                                                                       
Total params: 109 M                                                                                                
Total estimated model params size (MB): 437                                                                        
Modules in train mode: 0                                                                                           
Modules in eval mode: 231

Output()

Epoch 0, global step 293: 'val_loss' reached 0.69513 (best 0.69513), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\0-val_acc=0.7281.ckpt' as top 1
Epoch 1, global step 586: 'val_loss' reached 0.59755 (best 0.59755), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\1-val_acc=0.7537.ckpt' as top 1
Epoch 2, global step 879: 'val_loss' reached 0.52724 (best 0.52724), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\2-val_acc=0.8062.ckpt' as top 1
Epoch 3, global step 1172: 'val_loss' reached 0.48647 (best 0.48647), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\3-val_acc=0.8190.ckpt' as top 1
Epoch 4, global step 1465: 'val_loss' reached 0.46376 (best 0.46376), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\4-val_acc=0.8254.ckpt' as top 1
Epoch 5, global step 1758: 'val_loss' reached 0.45230 (best 0.45230), saving model to 'C:\\1. Python\\LLM_mods_Research\\bert_checkpoints\\5-val_acc

In [8]:
from sklearn.metrics import classification_report

# Assuming `trainer` is your Trainer object and `model` is your trained LightningModule
predictions = trainer.predict(bert_model, test_dataloader)

all_preds = []
all_labels = []

# Assuming each prediction output contains a dict with 'preds' and 'labels' keys as in your model's validation_step
for output in predictions:
    preds = output['preds'].cpu()
    labels = output['labels'].cpu()
    all_preds.append(preds)
    all_labels.append(labels)

# Concatenate all the tensors
all_preds = torch.cat(all_preds)
all_labels = torch.cat(all_labels)

# Convert tensors to numpy arrays if needed
all_preds = all_preds.numpy()
all_labels = all_labels.numpy()

# Generate the report
bert_report = classification_report(all_labels, all_preds, target_names=['positive', 'neutral', 'negative'])
print(bert_report)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Output()

              precision    recall  f1-score   support

    positive       0.78      0.77      0.77       378
     neutral       0.69      0.67      0.68       496
    negative       0.91      0.92      0.91      1469

    accuracy                           0.84      2343
   macro avg       0.79      0.79      0.79      2343
weighted avg       0.84      0.84      0.84      2343



### CLASSIFICATION OF COMMENTS WITH GPT MODELS

#### FIRST ATTEMPT WITH GPT-4o

In [7]:
from models.LLM_Classifier import GPT_Classifier, validate_GPT_model

pred_labels_GPT_4o = GPT_Classifier(x_test, name_of_prompt='prompt_for_classification_airlines', GPT_model='gpt-4o')

  0%|                                                                                                                                             | 1/2343 [00:00<32:40,  1.19it/s]

1
Chosen label from GPT model is: 1


  0%|                                                                                                                                             | 2/2343 [00:01<24:20,  1.60it/s]

0
Chosen label from GPT model is: 0


  0%|▏                                                                                                                                            | 3/2343 [00:02<30:26,  1.28it/s]

...

2
Chosen label from GPT model is: 2


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 2342/2343 [19:59<00:00,  2.13it/s]

1
Chosen label from GPT model is: 1


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2343/2343 [19:59<00:00,  1.95it/s]

1
Chosen label from GPT model is: 1


In [8]:
pred_labels_GPT_transformed_4o = []
for idx in range(len(pred_labels_GPT_4o)):
    if pred_labels_GPT_4o[idx] == 0:
        pred_labels_GPT_transformed_4o.append('positive')
    elif pred_labels_GPT_4o[idx] == 1:
        pred_labels_GPT_transformed_4o.append('neutral')
    else:
        pred_labels_GPT_transformed_4o.append('negative')
        
    
cls_report_GPT_4o = validate_GPT_model(y_test, pred_labels_GPT_transformed_4o)

              precision    recall  f1-score   support

    negative       0.95      0.84      0.89      1469
     neutral       0.53      0.79      0.63       496
    positive       0.80      0.65      0.72       378

    accuracy                           0.80      2343
   macro avg       0.76      0.76      0.75      2343
weighted avg       0.84      0.80      0.81      2343



#### SECOND ATTEMPT WITH GPT-4o-mini

In [9]:
from models.LLM_Classifier import GPT_Classifier, validate_GPT_model

pred_labels_GPT_4o_mini = GPT_Classifier(x_test, name_of_prompt='prompt_for_classification_airlines', GPT_model='gpt-4o-mini')

  0%|                                                                                                                                             | 1/2343 [00:00<22:10,  1.76it/s]

'0'
Chosen label from GPT model is: 0


  0%|                                                                                                                                             | 2/2343 [00:01<33:08,  1.18it/s]

0
Chosen label from GPT model is: 0


  0%|▏                                                                                                                                            | 3/2343 [00:02<31:09,  1.25it/s]

...

'2'
Chosen label from GPT model is: 2


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 2342/2343 [22:11<00:00,  1.51it/s]

'1'
Chosen label from GPT model is: 1


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2343/2343 [22:11<00:00,  1.76it/s]

'1'
Chosen label from GPT model is: 1


In [10]:
pred_labels_GPT_transformed_4o_mini = []
for idx in range(len(pred_labels_GPT_4o_mini)):
    if pred_labels_GPT_4o_mini[idx] == 0:
        pred_labels_GPT_transformed_4o_mini.append('positive')
    elif pred_labels_GPT_4o_mini[idx] == 1:
        pred_labels_GPT_transformed_4o_mini.append('neutral')
    else:
        pred_labels_GPT_transformed_4o_mini.append('negative')
        
    
cls_report_GPT = validate_GPT_model(y_test, pred_labels_GPT_transformed_4o_mini)

              precision    recall  f1-score   support

    negative       0.96      0.81      0.88      1469
     neutral       0.54      0.79      0.64       496
    positive       0.77      0.79      0.78       378

    accuracy                           0.80      2343
   macro avg       0.76      0.80      0.77      2343
weighted avg       0.84      0.80      0.81      2343

